# KorSciDeBERTa 논문 초록 분류 베이스라인 모델 학습

참조한 코드: <a href="https://colab.research.google.com/github/patrickvonplaten/notebooks/blob/master/ODSC_2022_%F0%9F%A4%97_Transformers_Workshop.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
'''
#[필수]리눅스 터미널에서 본 코드 및 토크나이저 다운로드
#git clone https://huggingface.co/kisti/korscideberta
#cd korscideberta

#[필수]라이브러리 설치(Mecab 등 자세한 설치 방법은 KorSciDeBERTa환경설치+파인튜닝.pdf 참조)
!apt install git-lfs
!pip install datasets transformers[sentencepiece]
'''

## **Preprocess the dataset**

분류 모델 업로드를 위해 Huggingface 로그인(API 토큰을 입력): [Hugging Face account](https://huggingface.co/join)

KorSciDeBERTa 토크나이저(tokenization_korscideberta.py) 임포트. 영문 DeBERTa 토크나이저: [DeBERTa's Tokenizer](https://huggingface.co/docs/transformers/model_doc/deberta-v2#transformers.DebertaV2Tokenizer).

In [8]:
from datasets import load_dataset
import datasets
from huggingface_hub import notebook_login

notebook_login() #Huggingface 로그인
#토큰 예시: hf_jRjLZcSBibYHwUaTjiNUEeoJlFxhFkGM

model_repository = "kisti/korscideberta" #Huggingface 모델명 설정
from transformers import AutoTokenizer
from tokenization_korscideberta_v2 import DebertaV2Tokenizer
tokenizer = DebertaV2Tokenizer.from_pretrained(model_repository)
out = tokenizer.tokenize("<cls> 한국어 모델을 <s> 한국어 모델을 공유합니다. <s>")
print(str(out))

#데이터셋 로드
#data_files = {"train": "문장의미-균등저널/test.json", "test": "문장의미-균등저널/train.json", 'dev':'문장의미-균등저널/dev.json'}
#dataset = load_dataset('json', data_files=data_files)
dataset = load_dataset('csv', data_files='data/Abstract_Annotation_Data_tagsentence.csv', split='train')
dataset = dataset.shuffle(seed=42)
dataset = dataset.train_test_split(test_size=0.1)
print("dataset:", str(dataset))

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


['<cls>', '▁한국어', '▁모델', '을', '<s>', '▁한국어', '▁모델', '을', '▁공유', '합니다', '▁.', '<s>']


Found cached dataset csv (/home/kgm86/.cache/huggingface/datasets/csv/default-1dee5acf2626c113/0.0.0/6954658bab30a358235fa864b05cf819af0e179325c740e4bc853bcc7ec513e1)
Loading cached shuffled indices for dataset at /home/kgm86/.cache/huggingface/datasets/csv/default-1dee5acf2626c113/0.0.0/6954658bab30a358235fa864b05cf819af0e179325c740e4bc853bcc7ec513e1/cache-75768aa1cfcdf733.arrow


dataset: DatasetDict({
    train: Dataset({
        features: ['did', 'tag', 'sentence'],
        num_rows: 6055
    })
    test: Dataset({
        features: ['did', 'tag', 'sentence'],
        num_rows: 673
    })
})


In [9]:
#데이터셋을 토크나이징 후 저장
from datasets import ClassLabel
labels = [x for x in dataset['train']['tag']]
labels = list(set(labels))
labels.sort()
num_labels = len(labels)
print('Labels: '+str(labels)[:200])
ClassLabels = ClassLabel(num_classes=len(labels), names=labels)

def preprocess_function(example):
    output_dict = tokenizer('<cls>'+example["sentence"]+'<s>', max_length=512, truncation=True)
    output_dict['labels'] = ClassLabels.str2int(example['tag'])
    return output_dict
#tokenized_datasets = dataset.map(preprocess_function, batched=False, remove_columns=dataset["train"].column_names)
tokenized_datasets = dataset.map(preprocess_function, batched=False)
tokenized_datasets = tokenized_datasets.cast_column("labels", ClassLabel(names=labels))

#데이터셋 토크나이징 확인
random_id = 1
print("Input IDS:", tokenized_datasets["train"][random_id]["input_ids"])
print("Labels:", tokenized_datasets["train"][random_id]["labels"])
tokenized_datasets.save_to_disk('data/tok')

Labels: ['DE', 'EX', 'NOT', 'PR', 'RED', 'RES', 'SI']


Map:   0%|          | 0/6055 [00:00<?, ? examples/s]

Map:   0%|          | 0/673 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/6055 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/673 [00:00<?, ? examples/s]

Input IDS: [2, 2, 1111, 126239, 558, 15724, 352, 1778, 126239, 310, 126260, 729, 126234, 1022, 126240, 229, 1949, 126249, 23, 126236, 3, 1, 1]
Labels: 6


Saving the dataset (0/1 shards):   0%|          | 0/6055 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/673 [00:00<?, ? examples/s]

In [15]:
#KorSciDeBERTa 모델 로딩
from transformers import AutoModelForSequenceClassification

num_labels = len(labels)
def model_init():
    #return AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=6)
    #return AutoModelForSequenceClassification.from_pretrained(model_repository, num_labels=num_labels, hidden_dropout_prob=0.3, attention_probs_dropout_prob=0.25)
    return AutoModelForSequenceClassification.from_pretrained(model_repository, num_labels=num_labels, hidden_dropout_prob=0.1, attention_probs_dropout_prob=0.1)
model = model_init()

Some weights of DebertaV2ForSequenceClassification were not initialized from the model checkpoint at kkmkorea/checkpoint25000 and are newly initialized: ['pooler.dense.bias', 'classifier.bias', 'pooler.dense.weight', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Next, we load a data collator. A [data collator](https://huggingface.co/docs/transformers/main_classes/data_collator) is responsible for making sure each batch is correctly padded during training, which should happen dynamically since training samples are reshuffled before each epoch.

In [16]:
#DataCollator 확인
from transformers import DataCollatorWithPadding
data_collator = DataCollatorWithPadding(tokenizer=tokenizer)
from collections import Counter
print("Test:", Counter(tokenized_datasets["test"]["labels"]))

#정확도 척도
from datasets import load_metric
accuracy = load_metric("accuracy")

import numpy as np
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_classes = np.argmax(pred_logits, axis=-1)
    labels = np.asarray(pred.label_ids)
    acc = accuracy.compute(predictions=pred_classes, references=labels)
    return {"accuracy": acc["accuracy"]}

Test: Counter({4: 221, 1: 123, 5: 111, 0: 93, 3: 76, 6: 48, 2: 1})


The validation and test data sets are as balanced as they can be, so we can safely use accuracy here!

 Let's load the [accuracy metric](https://huggingface.co/metrics/accuracy) via the datasets library.

Next, we define the `compute_metrics` which will be applied to the predicted outputs of the model which is of type [`EvalPrediction`](https://huggingface.co/docs/transformers/main/en/internal/trainer_utils#transformers.EvalPrediction) and therefore exposes the model's predictions and the gold labels.
We compute the predicted label class by taking the `argmax` of the model's prediction before passing it alongside the gold labels to the accuracy metric.

Great, now all components required for training are ready and all that's left to do is to define the hyper-parameters of the `Trainer`. We need to make sure that the model checkpoints are uploaded to the Hugging Face Hub during training. By setting `push_to_hub=True`, this is done automatically at every `save_steps` via the convenient [`push_to_hub`](https://huggingface.co/docs/transformers/main/en/main_classes/trainer#transformers.Trainer.push_to_hub) method.

Besides, we define some standard hyper-parameters such as learning rate, warm-up steps and training epochs. We will log the loss every 500 steps and run evaluation every 5000 steps.

In [19]:
#training_args 설정
#다음 에러 발생시 output_dir을 변경하여 다시 시도
#MlflowException: Changing param values is not allowed. Param with key=

import gc
gc.collect()
from transformers import TrainingArguments
training_args = TrainingArguments(
    output_dir="deberta_sent4455",
    num_train_epochs=4, 
    #learning_rate=5e-5,
    learning_rate=1.5e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=8,
    weight_decay=0.01,  
    fp16=True,                       # Use mixed precision
    fp16_opt_level="01",             # mixed precision mode
    warmup_steps=500,
    logging_steps=200,
    save_steps=2000,
    eval_steps=500,
    push_to_hub=True,
    evaluation_strategy="steps",
)

In [20]:
#Trainer 설정 후 학습 시작
import gc
gc.collect()

from transformers import Trainer
trainer = Trainer(
    args=training_args,
    compute_metrics=compute_metrics,
    model=model,
    #tokenizer=tokenizer, #에러 유발: TypeError: save_vocabulary() got an unexpected keyword argument 'filename_prefix'
    data_collator=data_collator,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["test"]
)
train_metrics = trainer.train().metrics
trainer.save_metrics("train", train_metrics)
trainer.push_to_hub()
#### 파인튜닝 및 모델 업로드 완료

Cloning https://huggingface.co/kkmkorea/deberta_sent4455 into local empty directory.
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/data_parallel.py:30: UserWarning: 
    There is an imbalance between your GPUs. You may want to exclude GPU 1 which
    has less than 75% of the memory or cores of GPU 0. You can do so by setting
    the device_ids argument to DataParallel, or by setting the CUDA_VISIBLE_DEVICES
    environment variable.
  warnings.warn(imbalance_warn.format(device_ids[min_pos], device_ids[max_pos]))
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was

/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/data_parallel.py:30: UserWarning: 
    There is an imbalance between your GPUs. You may want to exclude GPU 1 which
    has less than 75% of the memory or cores of GPU 0. You can do so by setting
    the device_ids argument to DataParallel, or by setting the CUDA_VISIBLE_DEVICES
    environment variable.
  warnings.warn(imbalance_warn.format(device_ids[min_pos], device_ids[max_pos]))
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  wa

Upload file pytorch_model.bin:   0%|          | 1.00/704M [00:00<?, ?B/s]

Upload file runs/Aug09_15-49-35_deeplatform/events.out.tfevents.1691563784.deeplatform.3790494.1:   0%|       …

To https://huggingface.co/kkmkorea/deberta_sent4455
   08a3042..30123bb  main -> main

To https://huggingface.co/kkmkorea/deberta_sent4455
   30123bb..231b8b6  main -> main



'https://huggingface.co/kkmkorea/deberta_sent4455/commit/30123bb98433c0d175707d169d1ea7a2a93ecdd9'

## **Evaluate / Analyse the model**

학습된 파인튜닝 모델로 추론 및 평가하는 단계

Now that we have fine-tuned the model we need to be very careful about analyzing its performance. It's usually not enough to just look at basic metrics defining the quality of a model purely on a metric, such as *accuracy*.
The better approach is to find a metric that best describes the actual use case of the model.

Let's dive into evaluating the model 🤿.

In [21]:
#Huggingface에 업로드한 파인튜닝 모델 및 성능 확인
from transformers import AutoModelForSequenceClassification
model = AutoModelForSequenceClassification.from_pretrained("kkmkorea/deberta_sent4455") #위에서 학습한 파인튜닝 모델 경로&저장소
#model = AutoModelForSequenceClassification.from_pretrained("patrickvonplaten/deberta_v3_amazon_reviews")

trainer = Trainer(
    args=training_args,
    compute_metrics=compute_metrics,
    model=model,
    #tokenizer=tokenizer,
    data_collator=data_collator,
)

prediction_metrics = trainer.predict(tokenized_datasets["test"]).metrics
#prediction_metrics = trainer.predict(tokenized_datasets["validation"]).metrics
prediction_metrics

/media/hdd1/kkm/deberta/HF/deberta_sent4455 is already a clone of https://huggingface.co/kkmkorea/deberta_sent4455. Make sure you pull the latest changes with `repo.git_pull()`.
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/data_parallel.py:30: UserWarning: 
    There is an imbalance between your GPUs. You may want to exclude GPU 1 which
    has less than 75% of the memory or cores of GPU 0. You can do so by setting
    the device_ids argument to DataParallel, or by setting the CUDA_VISIBLE_DEVICES
    environment variable.
  warnings.warn(imbalance_warn.format(device_ids[min_pos], device_ids[max_pos]))
/home/kgm86/anaconda3/envs/deberta/lib/python3.9/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


{'test_loss': 0.6081676483154297,
 'test_accuracy': 0.812778603268945,
 'test_runtime': 4.4393,
 'test_samples_per_second': 151.601,
 'test_steps_per_second': 9.686}

The Trainer is not only an excellent class to train a model, but also to evaluate a model on a dataset. Let's instantiate the trainer with the same instances and functions as before, but this time there is no need to pass a training dataset.

We use the Trainer's [`predict`]( ) function to evaluate the model on the test dataset on the same metric 

And let's run the evaluation again with our new metric computation which is better suited for our use case.

It does seem to generalize quite well to real-world data 🔥

## Optimization

As soon as you think the model's performance is good enough for production it's all about making the model as memory efficient and fast as possible.

There are some obvious solutions to this like choosing the best suited accelerated hardware, *e.g.* better GPUs, making sure no gradients are computed during the forward pass, or lowering the precision, *e.g.* to float16. 

More advanced optimization methods include using open-source accelerator libraries such as [ONNX Runtime](https://onnxruntime.ai/index.html), [quantization](https://pytorch.org/docs/stable/quantization.html), and inference servers like [Triton](https://developer.nvidia.com/nvidia-triton-inference-server).

At Hugging Face, we have been working a lot to facilitate the optimization of models, especially with our open-source [Optimum library](https://huggingface.co/hardware). Optimum makes it extremely simple to optimize most 🤗 Transformers models.

If you're looking for **highly optimized** solutions which don't require any technical knowledge, you might be interested in one of Hugging Face's paid inference services:

- [Inference API](https://huggingface.co/inference-api)
- [Infinity](https://huggingface.co/infinity)